# Lab 4.1: Creación de *facts* personalizados en watsonx.governance

Los *facts* (hechos) de AI Factsheets son metadatos que describen las características de un modelo de IA. Estos *facts* se pueden utilizar para proporcionar información sobre el modelo, como su propósito, su rendimiento y sus limitaciones.

En este lab, utilizaremos el SDK de Python para el servicio de [AI Factsheets]() de watsonx.governance para crear *facts* de nuestro prompt template personalizados a los necesidades/requisitos de nuestro negocio u organización.

Es importante resaltar que los *facts* de un modelo o prompt se diferencia de sus *metricas*. Toda métrica es un fact, pero no todos los facts son métricas. Decimos que las métricas son medidas **cuantitativas** del rendimiento del modelo que pueden ser evaluadas, monitorizadas, y que generalmente queremos optimizar. Por ejemplo, la precisión, la recuperación y la puntuación F1 son métricas. En cambio, los *facts* son medidas que pueden ser tanto cuantitativas como **cualitativas** que describen las características del modelo. Por ejemplo, el propósito del modelo, la fecha en que fue creado, su rendimiento en diferentes métricas, grupos demográficos objetivos, y sus limitaciones son *facts*.

In [ ]:
# importa las librerías necesarias
import os
import tempfile
import time
import pandas as pd
from ibm_aigov_facts_client import AIGovFactsClient, CloudPakforDataConfig
from ibm_watsonx_ai import Credentials, APIClient as WatsonxAIClient
from ibm_watsonx_ai.foundation_models.prompts import PromptTemplateManager
from IPython.display import display, Markdown

Configuración de las credenciales:

In [3]:
API_KEY = "<YOUR API KEY HERE>"
URL = "<YOUR URL HERE>"
USERNAME = "<YOUR USERNAME HERE>"
PASSWORD = "<YOUR PASSWORD HERE>"
# si ejecutas desde un entorno de IBM Cloud Pak for Data, puedes obtener el PROJECT_ID de la variable de entorno PROJECT_ID
PROJECT_ID = os.getenv('PROJECT_ID', "<YOUR PROJECT ID HERE>")

creds = Credentials(
    api_key=API_KEY,
    url=URL,
    username=USERNAME,
    password=PASSWORD,
    instance_id="openshift"
)
# Inicialización de clientes
watsonx_ai_client = WatsonxAIClient(credentials=creds, project_id=PROJECT_ID)
facts_client = AIGovFactsClient(
    cloud_pak_for_data_configs=CloudPakforDataConfig(
        service_url=URL,
        username=USERNAME,
        api_key=API_KEY,
    ),
    container_id=PROJECT_ID,
    container_type="project",
    disable_tracing=True,
)

Lista los prompt templates disponibles en el proyecto:

In [ ]:
prompt_mgr = PromptTemplateManager(api_client=watsonx_ai_client, project_id=PROJECT_ID)

# List prompt templates
templates_df = prompt_mgr.list(limit=5)  # Lista 5 templates más recientes
templates_df

Selecciona el prompt template a utilizar (en este caso, el que creamos en el lab 3):

In [ ]:
# selecciona el prompt template a utilizar
prompt_template_id = templates_df.iloc[0]['ID'] #"<ID DEL PROMPT TEMPLATE>"
print(f"{prompt_template_id=}")
# obten detalles del prompt template
prompt_template = facts_client.assets.get_model(prompt_template_id)
prompt_template

## Creación de *facts* personalizados para prompt templates o modelos de IA

Para crear un *fact* personalizado en watsonx.governance, debemos primero definir los detalles del *fact* que queremos crear. Estos detalles incluyen el nombre del *fact*, su descripción, su tipo, valor por defecto, etc.

**Nota:** Los custom facts son creados globalmente, por lo que estarán disponibles para todos los prompt templates ubicados en el mismo entorno. Por lo tanto, es importante que los nombres de los *facts* sean únicos y descriptivos. 

**Acción: En la siguiente celda deberás de fijar un prefijo único para los *facts* que crearemos en este lab. Puede ser tu nombre de usuario, las inicialies de tu nombre, o cualquier otro prefijo que te ayude a identificar los *facts* que crees.**

In [28]:
# evita usar espacio en blanco en el prefijo, así como letras mayúsculas y caracteres especiales
USER_PREFIX = "<tu_prefijo_de_usuario_aqui>" # ejemplo: "juanperez", "ssv", "jdoe"

In [29]:
# definimos la clase que representa la definición de un 'fact' en IBM AI Factsheets
from dataclasses import dataclass
from typing import Literal

@dataclass 
class FactDefinition:
    name: str
    type: Literal["integer", "string", "date"]
    description: str
    placeholder: str = ""
    is_array: bool = False
    required: bool = False
    hidden: bool = False
    readonly: bool = False
    default_value: int = 0
    label: str = None
    minimum: int = None
    maximum: int = None
    min_length: int = None
    max_length: int = None
    is_searchable: bool = True

    def __post_init__(self):
        self.name = f"{USER_PREFIX}_{self.name}"
        if self.label is None:
            self.label = self.name

Vamos a crear tres custom facts en base a los criterios definidos por nuestra organización para la governanza de casos de uso de IA generativa:

- **project_manager**: el nombre del manager en la organización encargado del proyecto para el cual se está creando el prompt template.
- **grc_compliance**: el nombre del equipo de GRC (Governance, Risk and Compliance) encargado de revisar y aprobar el prompt template.
- **grc_ticket_id**: el ID del ticket de GRC que se creó para revisar y aprobar el prompt template correspondiente.

In [ ]:
# Vamos a tres custom facts en base a los criterios definidos por nuestra organización para la governanza de casos de uso de IA generativa:

# - **project_manager**: el nombre del manager en la organización encargado del proyecto para el cual se está creando el prompt template.
# - **grc_compliance**: el nombre del equipo de GRC (Governance, Risk and Compliance) encargado de revisar y aprobar el prompt template.
# - **grc_ticket_id**: el ID del ticket de GRC que se creó para revisar y aprobar el caso de uso de IA generativa.

custom_facts = [
    FactDefinition(
        name="project_manager",
        type="string",
        description=USER_PREFIX+" The name of the project manager responsible for the generative AI use case.",
        placeholder=USER_PREFIX+" project manager's name",
        required=True,
    ),
    FactDefinition(
        name="grc_compliance",
        type="string",
        description=USER_PREFIX+" The name of the GRC team responsible for reviewing and approving the generative AI use case.",
        placeholder=USER_PREFIX+" GRC team's name",
        required=True,
    ),
    FactDefinition(
        name="grc_ticket_id",
        type="string",
        description="The ID of the GRC ticket created for reviewing and approving the generative AI use case.",
        placeholder=USER_PREFIX+" GRC ticket ID",
        required=False,
    ),
]
custom_facts_df = pd.DataFrame(custom_facts)
custom_facts_df

In [ ]:
# damos de alta a los custom facts en la plataforma
# create_custom_facts_definitions acepta un csv con la definición de los custom facts
# así que vamos a crear un archivo temporal con la definición de los custom facts para poder subirlo
with tempfile.NamedTemporaryFile() as f:
    custom_facts_df.to_csv(f, index=False)
    facts_client.assets.create_custom_facts_definitions(f.name, overwrite=False)
time.sleep(3) # espera 3 segundos para que los custom facts se creen

### Obten todas las definiciones de *facts* disponibles:

In [ ]:
facts_client.assets.get_facts_definitions(type_name="modelfacts_user")

### Establece el valor de los *facts* personalizados para el prompt template seleccionado:

Sientete libre de modificar los valores de los *facts* personalizados para ayudarte a identificarlos en la fact sheet del prompt template.

In [ ]:
prompt_template = facts_client.assets.get_model(prompt_template_id)
prompt_template.set_custom_fact(USER_PREFIX+"_project_manager", "John Doe") # cambia "John Doe" por otro nombre
prompt_template.set_custom_fact(USER_PREFIX+"_grc_compliance", "GRC Team 1")  
prompt_template.set_custom_fact(USER_PREFIX+"_grc_ticket_id", "GRC-123") 

In [ ]:
# Tambien podemos hacer lo mismo para multiples facts en una sola llamada (sobreescribira los valores anteriores)
prompt_template.set_custom_facts({
    USER_PREFIX+"_grc_compliance": "GRC Team 1", # cambia "GRC Team 1" por otro nombre
    USER_PREFIX+"_grc_ticket_id": "GRC-123", # cambia "GRC-123" por otro valor
})

Visualiza los custom facts creados en la plataforma. Los custom facts deberían aparecer en el apartado 'Additional details' de la AI Factsheet del prompt template seleccionado.

**Acción**: Pulsa el link generado abajo para visualizar los custom facts creados en la plataforma.

In [ ]:
factsheets_url = f"{creds.url}/wx/prompt-details/{prompt_template._asset_id}/factsheet?context=wx&project_id={PROJECT_ID}"
display(Markdown(f"[Pulsa aquí para ver la AI Factsheet en la plataforma]({factsheets_url})"))

Tambien puedes obtener los facts de un prompt template o modelo particular utilizando los métodos `get_custom_facts` o `get_all_facts` del SDK de Python.

In [ ]:
prompt_template.get_custom_facts()

In [ ]:
prompt_template.get_all_facts()

### Eliminar *facts* personalizados

Hasta ahora, hemos creado custom facts en watsonx.governance. Ahora, vamos a ver como eliminar algunos de los custom facts que hemos creado. Esto es útil si queremos actualizar o modificar un custom fact existente, o si queremos eliminar un custom fact que ya no es necesario.

In [ ]:
prompt_template.remove_custom_fact(USER_PREFIX+"_grc_ticket_id")
prompt_template.get_custom_facts()

In [ ]:
# remover multiples facts en una sola llamada
prompt_template.remove_custom_facts([USER_PREFIX+"_project_manager", USER_PREFIX+"_grc_compliance"])
prompt_template.get_custom_facts()

Visualiza los custom facts creados en la plataforma. Los custom facts deberían aparecer en el apartado 'Additional details' de la AI Factsheet del prompt template seleccionado.

**Acción**: Pulsa el link generado abajo para visualizar los custom facts creados en la plataforma.

In [ ]:
factsheets_url = f"{creds.url}/wx/prompt-details/{prompt_template._asset_id}/factsheet?context=wx&project_id={PROJECT_ID}"
display(Markdown(f"[Pulsa aquí para ver la AI Factsheet en la plataforma]({factsheets_url})"))

## Facts personalizados para casos de uso

Además de los requisitos antes mencionados para el uso de modelos de IA generativa, nuestra organización también requiere que en cada caso de uso de IA, debe estar registrado el **cliente** para el que se está creando ese caso de uso (si aplicable), y el **equipo de desarrollo** que está trabajando en el caso de uso.

<!-- Algunas organizaciones pueden requerir la creación de *facts* personalizados no solo al nivel granular de modelo o prompt template, sino también al nivel de casos de uso. En este caso, los *facts* personalizados se pueden utilizar para describir las características de un caso de uso específico más allá de las que estan cubiertas por las que viene en la plataforma, como el cliente para el que se está creando, el equipo de desarrollo, etc. -->

La API de AI Factsheets de watsonx.governance permite la creación de *facts* personalizados no solo a nivel de modelo o prompt template, sino también a nivel de casos de uso. Dado esto, Para cumplir con la normativa de nuestra organización, vamos a crear dos custom facts adicionales:

- **cliente**: el nombre del cliente para el que se está creando el caso de uso de IA generativa.
- **equipo_desarrollo**: el nombre del equipo de desarrollo que está trabajando en el caso de uso de IA generativa.


Obtenemos el caso de uso de IA generativa que queremos actualizar:

In [ ]:
ai_usecase = prompt_template.get_tracking_model_usecase()
ai_usecase

In [ ]:
usecase_custom_facts = [
    FactDefinition(
        name="Cliente",
        type="string",
        description="El nombre del cliente para el cual se está creando el caso de uso de IA generativa.",
        placeholder="nombre del cliente",
        required=False,
    ),
    FactDefinition(
        name="Equipo de Desarrollo",
        type="string",
        description="El nombre del equipo de desarrollo que está trabajando en el caso de uso de IA generativa.",
        placeholder="nombre del equipo de desarrollo",
        required=False,
    ),
]
usecase_custom_facts_df = pd.DataFrame(usecase_custom_facts)
usecase_custom_facts_df

Damos de alta a los custom facts para casos de uso en la plataforma. 

In [ ]:
with tempfile.NamedTemporaryFile() as f:
    usecase_custom_facts_df.to_csv(f, index=False)
    facts_client.assets.create_custom_facts_definitions(f.name, overwrite=False, type_name="model_entry_user")
time.sleep(5)

In [ ]:
facts_client.assets.get_facts_definitions(type_name="model_entry_user")

In [ ]:
# facts_client.assets.get_model_usecases()
ai_usecase._facts_definitions = None
ai_usecase.set_custom_fact(USER_PREFIX+"_Cliente", "Telefonica España")
ai_usecase.set_custom_fact(USER_PREFIX+"_Equipo de Desarrollo", "Equipo de IA de Telefonica")

Visualiza los custom facts creados en la plataforma. Los custom facts deberían aparecer en el apartado 'Details' del caso de uso seleccionado.

**Acción**: Pulsa el link generado abajo para visualizar los custom facts creados en la plataforma.

In [ ]:
usecase_factsheets_url = f"{creds.url}/aigov/modelinventory/inventories/{ai_usecase._container_id}/aiusecase/{ai_usecase._asset_id}?context=wx"
display(Markdown(f"[Pulsa aquí para ver el AI Use Case en la plataforma]({usecase_factsheets_url})"))

In [ ]:
ai_usecase.get_custom_facts()

### Remueve los custom facts del caso de uso

In [ ]:
ai_usecase.remove_custom_facts([USER_PREFIX+"_Cliente", USER_PREFIX+"_Equipo de Desarrollo"])
ai_usecase.get_custom_facts()

**Acción**: Pulsa el link generado abajo para comprobar que los valores de tus *facts* personalizados no te aparecen en el caso de uso seleccionado.

In [ ]:
usecase_factsheets_url = f"{creds.url}/aigov/modelinventory/inventories/{ai_usecase._container_id}/aiusecase/{ai_usecase._asset_id}?context=wx"
display(Markdown(f"[Pulsa aquí para ver el AI Use Case en la plataforma]({usecase_factsheets_url})"))